# Reinforcement Learning control strategies for Electric Vehicles fleet Virtual Power Plants
Thesis based on the development of a RL agent that manages a VPP through EVs charging stations in an household environment. Main optimization objectives of the VPP are: Valley filling, peak shaving and zero resulting load over time. Main action performed to reach objectives are: storage of Renewable energy resources and power push in the grid at high demand times. The development of the Virtual Power Plant environment is based on the ELVIS (Electric Vehicles Infrastructure Simulator) open library from DAI-Labor: https://github.com/dailab/elvis The thesis code is currently available at: (https://github.com/francescomaldonato/RL_VPP_Thesis)

Author: Francesco Maldonato

## VPP simulator Notebook based on EVs arrival, with StableBaselines3 trained model
(Recurrent PPO) [default: 25 EVs per week simulation]

Installing required packages and dependencies

In [65]:
%%capture
!pip install py-elvis==0.2.1
!pip install pyyaml==5.4
!pip install plotly==5.9.0
!pip install -U kaleido==0.2.1

!pip install stable-baselines3[extra]==1.6.1
!pip install stable-baselines==1.6.1
!pip install sb3-contrib==1.6.1
!pip install gym==0.20.0
!pip install -q wandb==0.13.4

In [66]:
#Cloning repository and changing directory
!git clone https://github.com/francescomaldonato/RL_VPP_Thesis.git
%cd RL_VPP_Thesis/
%ls

In [68]:
import yaml
import numpy as np
from gym import Env
from VPP_environment import VPPEnv, VPP_Scenario_config
from elvis.config import ScenarioConfig
import os
import torch
import random
import wandb
from sb3_contrib import RecurrentPPO #The available algoritmhs in sb3-contrib for the custom environment with MultiInputPolicy
from sb3_contrib.common.maskable.utils import get_action_masks
import stable_baselines3 as sb3
from stable_baselines3.common.env_checker import check_env

#Check if cuda device is available for training
print("Torch-Cuda available device:", torch.cuda.is_available())
print(sb3.get_system_info())
#!wandb --version

Torch-Cuda available device: False
OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022
Python: 3.7.14
Stable-Baselines3: 1.6.1
PyTorch: 1.12.1+cu113
GPU Enabled: False
Numpy: 1.21.6
Gym: 0.20.0

({'OS': 'Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022', 'Python': '3.7.14', 'Stable-Baselines3': '1.6.1', 'PyTorch': '1.12.1+cu113', 'GPU Enabled': 'False', 'Numpy': '1.21.6', 'Gym': '0.20.0'}, 'OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022\nPython: 3.7.14\nStable-Baselines3: 1.6.1\nPyTorch: 1.12.1+cu113\nGPU Enabled: False\nNumpy: 1.21.6\nGym: 0.20.0\n')


In [69]:
# Ensure deterministic behavior
torch.backends.cudnn.deterministic = True
random.seed(0)
torch.manual_seed(0)
torch.cuda.manual_seed_all(0)

## Load ELVIS YAML config file
Section where the EVs arrival simulation parameters are loaded through the Yaml config file from the 'data/config_builder/' folder.

In [70]:
#Loading paths for input data
current_folder = ''
VPP_training_data_input_path = current_folder + 'data/data_training/environment_table/' + 'Environment_data_2019.csv'
VPP_testing_data_input_path = current_folder + 'data/data_testing/environment_table/' + 'Environment_data_2020.csv'
VPP_validating_data_input_path = current_folder + 'data/data_validating/environment_table/' + 'Environment_data_2018.csv'
elvis_input_folder = current_folder + 'data/config_builder/'

#case = 'wohnblock_household_simulation_adaptive.yaml' #(loaded by default, 20 EVs arrivals per week with 50% average battery)

#Try different simulation parameters, uncomment below
#case = 'wohnblock_household_simulation_adaptive_10.yaml' #(10 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_15.yaml' #(15 EVs arrivals per week with 50% average battery)
case = 'wohnblock_household_simulation_adaptive_25.yaml' #(25 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_30.yaml' #(30 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_35.yaml' #(35 EVs arrivals per week with 50% average battery) 

with open(elvis_input_folder + case, 'r') as file:
    yaml_str = yaml.full_load(file)

elvis_config_file = ScenarioConfig.from_yaml(yaml_str)
VPP_config_file = VPP_Scenario_config(yaml_str)

print(elvis_config_file)
print(VPP_config_file)

Vehicle types: <generator object ScenarioConfig.__str__.<locals>.<genexpr> at 0x7f4251190250>Mean parking time: 23.99
Std deviation of parking time: 1
Mean value of the SOC distribution: 0.5
Std deviation of the SOC distribution: 0.1
Max parking time: 24
Number of charging events per week: 25
Vehicles are disconnected only depending on their parking time
Queue length: 0
Opening hours: None
Scheduling policy: Uncontrolled

{'start_date': '2022-01-01T00:00:00', 'end_date': '2023-01-01T00:00:00', 'resolution': '0:15:00', 'num_households': 4, 'solar_power': 16, 'wind_power': 12, 'EV_types': [{'battery': {'capacity': 100, 'efficiency': 1, 'max_charge_power': 150, 'min_charge_power': 0}, 'brand': 'Tesla', 'model': 'Model S', 'probability': 1}], 'charging_stations_n': 4, 'EVs_n': 25, 'EVs_n_max': 1305, 'mean_park': 23.99, 'std_deviation_park': 1, 'EVs_mean_soc': 50.0, 'EVs_std_deviation_soc': 10.0, 'EV_load_max': 44, 'EV_load_rated': 14.8, 'EV_load_min': 1, 'houseRWload_max': 10, 'av_max_ener

In [71]:
#TESTING Environment initialization
env = VPPEnv(VPP_testing_data_input_path, elvis_config_file, VPP_config_file)
env.plot_VPP_input_data()

Output hidden; open in https://colab.research.google.com to view.

In [72]:
env.plot_ELVIS_data()

In [73]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
env.plot_reward_functions()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  26933.24 , over-consume=kWh  42949.25 , under-consume=kWh  16016.01 , Total_cost=€  1051.05 , overcost=€  1512.84 , Av.EV_en_left=kWh  100.0 , Charging_events=  1304 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  70.06
Simulating VPP....


### VPP Simulation test with random actions [no model loaded]

In [74]:
episodes = 1
for episode in range(1, episodes+1):
    state = env.reset()
    done = False
    score = 0
    while not done:
        action_masks = get_action_masks(env)
        action = env.action_space.sample()
        
        n_state, reward, done, info = env.step(action)
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [75]:
env.plot_Elvis_results()

Output hidden; open in https://colab.research.google.com to view.

In [76]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [77]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [78]:
env.plot_VPP_Elvis_comparison()

In [79]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
#env.plot_rewards_stats()

In [81]:
env.plot_EVs_kpi()

In [82]:
env.plot_actions_kpi()

In [83]:
env.plot_load_kpi()

In [84]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [85]:
## Wandb login to load models
#In Colab, uncomment below:
# %env "WANDB_DISABLE_CODE" True
# %env "WANDB_NOTEBOOK_NAME" "VPP_simulator.ipynb"
# os.environ['WANDB_NOTEBOOK_NAME'] = 'VPP_simulator.ipynb'
#wandb.login(relogin=True)

#In local notebook, uncomment below:
#your_wandb_login_code = 0123456789abcdefghijklmnopqrstwxyzàèìòù0 #example length
#!wandb login {your_wandb_login_code}

In [86]:
#Loading training model, from local directory or from wandb previous trainings
RecurrentPPO_path = "trained_models/RecurrentPPO_models/model_RecurrentPPO_"

#model_id = "s37o8q0n"
model_id = "333ckz0i"
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

# run_id_restore = "2y2dqvyn"
# model = wandb.restore(f'model_{run_id_restore}.zip', run_path=f"francesco_maldonato/RL_VPP_Thesis/{run_id_restore}")

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



## Testing dataset VPP Simulation using the loaded trained model

In [87]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

#Save the VPP table
VPP_table = env.save_VPP_table(save_path='data/environment_optimized_output/VPP_table.csv')

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  27625.9 , over-consume=kWh  44046.46 , under-consume=kWh  16420.56 , Total_cost=€  1070.48 , overcost=€  1545.79 , Av.EV_en_left=kWh  100.0 , Charging_events=  1304 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  70.06
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -1489.51 , over-consume=KWh  1743.65 , under-consume=KWh  3233.16 , Total_cost=€  -25.84 , Overcost=€  60.43 
 EV_INFO: Av.EV_energy_leaving=kWh  65.19 , Std.EV_energy_leaving=kWh  23.76 , EV_departures =  1306 , EV_queue_left =  0
SCORE:  Cumulative_reward= 468422.54 - Step_rewars (load_t= 420184.06, EVs_energy_t= 16111.91)
 - Final_rewards (EVs_energy= 20275.68, Overconsume= -799.46, Underconsume= 77.57, Overcost= 12572.77)
Episode:1 Score:468422.5394323875


In [88]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [89]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00  49.160137  64.024704  65.659584  44.765965   
2022-01-01 00:15:00  49.410137  63.341290  64.976166  45.015965   
2022-01-01 00:30:00  49.660137  62.830078  64.464951  45.265965   
2022-01-01 00:45:00  49.910137  62.152977  63.787849  45.515965   
2022-01-01 01:00:00  50.160137  61.768467  63.403339  45.765965   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  74.134613   0.000000   0.000000  67.038719   
2022-06-06 05:00:00  75.654167   0.000000   0.000000  68.558273   
2022-06-06 05:15:00  76.750748   0.000000   0.000000   0.000000   
2022-06-06 05:30:00  79.500748   0.000000   0.000000   0.000000   
2022-06-06 05:45:00  82.250748   0.000000   0.000000   0.000000   

                                           EVs_id       actions  \
time                                                              
2022-01-01 00:00:00                  [0, 0, 0, 0]  [1, 2, 2, 1]   
2022-01-01 00:15:00  [14339, 14342, 14341, 14340]  [1, 2, 2, 1]   
2022-01-01 00:30:00  [14339, 14342, 14341, 14340]  [1, 2, 2, 1]   
2022-01-01 00:45:00  [14339, 14342, 14341, 14340]  [1, 2, 2, 1]   
2022-01-01 01:00:00  [14339, 14342, 14341, 14340]  [1, 2, 2, 1]   
...                                           ...           ...   
2022-06-06 04:45:00          [14887, 0, 0, 14886]  [1, 2, 2, 1]   
2022-06-06 05:00:00          [14887, 0, 0, 14886]  [1, 1, 2, 1]   
2022-06-06 05:15:00              [14887, 0, 0, 0]  [1, 2, 0, 0]   
2022-06-06 05:30:00              [14887, 0, 0, 0]  [1, 2, 0, 0]   
2022-06-06 05:45:00              [14887, 0, 0, 0]  [1, 2, 0, 0]   

                                       mask_truth          load  load_reward  \
time                                                                           
2022-01-01 00:00:00  [False, False, False, False]  1.300694e+00    15.000000   
2022-01-01 00:15:00    [False, True, True, False] -4.440892e-16    15.000000   
2022-01-01 00:30:00    [False, True, True, False]  0.000000e+00    15.000000   
2022-01-01 00:45:00    [False, True, True, False]  0.000000e+00    15.000000   
2022-01-01 01:00:00    [False, True, True, False]  0.000000e+00    15.000000   
...                                           ...           ...          ...   
2022-06-06 04:45:00    [True, False, False, True] -2.649955e+00    15.000000   
2022-06-06 05:00:00    [True, False, False, True]  0.000000e+00    -5.351213   
2022-06-06 05:15:00     [True, False, True, True] -4.386334e+00    -0.073637   
2022-06-06 05:30:00     [True, False, True, True] -1.044182e+00    -0.952184   
2022-06-06 05:45:00     [True, False, True, True] -1.571310e+00     2.850180   

                     EV_reward    rewards  
time                                       
2022-01-01 00:00:00    0.00000  15.000000  
2022-01-01 00:15:00    0.00000  15.000000  
2022-01-01 00:30:00    0.00000  15.000000  
2022-01-01 00:45:00    0.00000  15.000000  
2022-01-01 01:00:00    0.00000  15.000000  
...                        ...        ...  
2022-06-06 04:45:00    0.00000  15.000000  
2022-06-06 05:00:00   53.36057  48.009357  
2022-06-06 05:15:00    0.00000  -0.073637  
2022-06-06 05:30:00    0.00000  -0.952184  
2022-06-06 05:45:00    0.00000   2.850180  

[15000 rows x 11 columns]

In [90]:
#env.plot_Elvis_results()

In [91]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [92]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [93]:
env.plot_VPP_Elvis_comparison()

In [94]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [95]:
env.plot_rewards_stats()

In [96]:
env.plot_EVs_kpi()

In [97]:
env.plot_load_kpi()

In [98]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Validating dataset VPP Simulation using the loaded trained model

In [99]:
#VALIDATING Environment initialization
env = VPPEnv(VPP_validating_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 15647, Arrival time: 2022-01-01 10:45:00, Parking_time: 23.83683597353989, Leaving_time: 2022-01-02 10:35:12.609505, SOC: 0.6055982353414125, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 16950, Arrival time: 2022-12-31 18:00:00, Parking_time: 24, Leaving_time: 2023-01-01 18:00:00, SOC: 0.5478347785558709, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -30085.39 , over-consume=kWh  2136.67 , under-consume=kWh  -32222.06 , Total_cost=€  -1187.15 , overcost=€  113.34
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  18233.17 , over-consume=kWh  38475.95 , under-consume=kWh  20242.78 , Total_cost=€  866.84 , overcost=€  1685.3 , Charging_events=  1304 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  74.71


In [100]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [101]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [102]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  18433.18 , over-consume=kWh  38948.93 , under-consume=kWh  20515.75 , Total_cost=€  877.19 , overcost=€  1702.15 , Av.EV_en_left=kWh  100.0 , Charging_events=  1304 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  74.71
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -4933.79 , over-consume=KWh  1106.84 , under-consume=KWh  6040.63 , Total_cost=€  -181.86 , Overcost=€  48.71 
 EV_INFO: Av.EV_energy_leaving=kWh  69.07 , Std.EV_energy_leaving=kWh  23.25 , EV_departures =  1301 , EV_queue_left =  0
SCORE:  Cumulative_reward= 451889.07 - Step_rewars (load_t= 387891.53, EVs_energy_t= 30681.5)
 - Final_rewards (EVs_energy= 20867.13, Overconsume= -343.58, Underconsume= -1770.72, Overcost= 14563.21)
Episode:1 Score:451889.0701947906


In [103]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [104]:
VPP_table.head(15000)

0          1          2    3  \
time                                                        
2022-01-01 00:00:00   0.000000   0.000000   0.000000  0.0   
2022-01-01 00:15:00   0.000000   0.000000   0.000000  0.0   
2022-01-01 00:30:00   0.000000   0.000000   0.000000  0.0   
2022-01-01 00:45:00   0.000000   0.000000   0.000000  0.0   
2022-01-01 01:00:00   0.000000   0.000000   0.000000  0.0   
...                        ...        ...        ...  ...   
2022-06-06 04:45:00   0.000000  66.513458  91.494286  0.0   
2022-06-06 05:00:00   0.000000  68.301430  93.282257  0.0   
2022-06-06 05:15:00  69.000694  70.127686  95.108513  0.0   
2022-06-06 05:30:00  70.697899  70.127686  96.805717  0.0   
2022-06-06 05:45:00  72.450966  70.127686  98.558784  0.0   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:15:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:30:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:45:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 01:00:00              [0, 0, 0, 0]  [2, 0, 1, 0]   
...                                       ...           ...   
2022-06-06 04:45:00      [0, 18788, 18787, 0]  [2, 1, 1, 2]   
2022-06-06 05:00:00      [0, 18788, 18787, 0]  [2, 1, 1, 2]   
2022-06-06 05:15:00  [18789, 18788, 18787, 0]  [1, 0, 1, 2]   
2022-06-06 05:30:00  [18789, 18788, 18787, 0]  [1, 0, 1, 2]   
2022-06-06 05:45:00  [18789, 18788, 18787, 0]  [1, 0, 1, 2]   

                                      mask_truth      load  load_reward  \
time                                                                      
2022-01-01 00:00:00  [False, False, False, True] -2.777890    -5.118074   
2022-01-01 00:15:00  [False, False, False, True] -4.129881    -5.272501   
2022-01-01 00:30:00  [False, False, False, True] -4.299751    -3.205998   
2022-01-01 00:45:00  [False, False, False, True] -2.923599    -4.546202   
2022-01-01 01:00:00   [False, True, False, True] -3.727721    -5.252454   
...                                          ...       ...          ...   
2022-06-06 04:45:00  [False, True, False, False]  0.000000    15.000000   
2022-06-06 05:00:00  [False, True, False, False]  0.000000    15.000000   
2022-06-06 05:15:00   [True, True, False, False]  0.000000    15.000000   
2022-06-06 05:30:00  [True, False, False, False]  0.000000    15.000000   
2022-06-06 05:45:00  [True, False, False, False]  0.000000    -1.430480   

                     EV_reward    rewards  
time                                       
2022-01-01 00:00:00        0.0  -5.118074  
2022-01-01 00:15:00        0.0  -5.272501  
2022-01-01 00:30:00        0.0  -3.205998  
2022-01-01 00:45:00        0.0  -4.546202  
2022-01-01 01:00:00        0.0  -5.252454  
...                        ...        ...  
2022-06-06 04:45:00        0.0  15.000000  
2022-06-06 05:00:00        0.0  15.000000  
2022-06-06 05:15:00        0.0  15.000000  
2022-06-06 05:30:00        0.0  15.000000  
2022-06-06 05:45:00        0.0  -1.430480  

[15000 rows x 11 columns]

In [105]:
env.plot_VPP_results()


Output hidden; open in https://colab.research.google.com to view.

In [106]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [107]:
env.plot_VPP_Elvis_comparison()

In [108]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [109]:
env.plot_rewards_stats()

In [110]:
env.plot_EVs_kpi()

In [111]:
env.plot_load_kpi()

In [112]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Training dataset VPP Simulation using the loaded trained model

In [113]:
#TRAINING Environment initialization
env = VPPEnv(VPP_training_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 19559, Arrival time: 2022-01-01 00:45:00, Parking_time: 23.868574656579703, Leaving_time: 2022-01-02 00:37:06.868764, SOC: 0.40642747485206804, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 20862, Arrival time: 2022-12-31 15:00:00, Parking_time: 22.897401644027724, Leaving_time: 2023-01-01 13:53:50.645918, SOC: 0.508158027751728, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -34117.7 , over-consume=kWh  1556.25 , under-consume=kWh  -35673.95 , Total_cost=€  -1196.64 , overcost=€  97.86
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  14440.91 , over-consume=kWh  36238.42 , under-consume=kWh  21797.51 , Total_cost=€  720.88 , overcost=€  1519.57 , Charging_events=  1304 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  77.36


In [114]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [115]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [116]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  13579.51 , over-consume=kWh  35499.95 , under-consume=kWh  21920.44 , Total_cost=€  679.94 , overcost=€  1486.4 , Av.EV_en_left=kWh  100.0 , Charging_events=  1304 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  77.36
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -6270.44 , over-consume=KWh  766.25 , under-consume=KWh  7036.69 , Total_cost=€  -223.2 , Overcost=€  32.59 
 EV_INFO: Av.EV_energy_leaving=kWh  72.01 , Std.EV_energy_leaving=kWh  22.83 , EV_departures =  1299 , EV_queue_left =  1
SCORE:  Cumulative_reward= 458388.19 - Step_rewars (load_t= 380552.18, EVs_energy_t= 42154.43)
 - Final_rewards (EVs_energy= 22180.46, Overconsume= -64.67, Underconsume= -2268.95, Overcost= 15834.74)
Episode:1 Score:458388.185778549


In [117]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [118]:
VPP_table.head(14995)

0          1    2          3                EVs_id  \
time                                                                        
2022-01-01 00:00:00  0.0   0.000000  0.0   0.000000          [0, 0, 0, 0]   
2022-01-01 00:15:00  0.0   0.000000  0.0   0.000000          [0, 0, 0, 0]   
2022-01-01 00:30:00  0.0   0.000000  0.0   0.000000          [0, 0, 0, 0]   
2022-01-01 00:45:00  0.0   0.000000  0.0   0.000000          [0, 0, 0, 0]   
2022-01-01 01:00:00  0.0   0.000000  0.0   0.000000          [0, 0, 0, 0]   
...                  ...        ...  ...        ...                   ...   
2022-06-06 03:30:00  0.0  80.987358  0.0  88.161728  [0, 22732, 0, 22733]   
2022-06-06 03:45:00  0.0  81.571350  0.0  88.745720  [0, 22732, 0, 22733]   
2022-06-06 04:00:00  0.0  82.304947  0.0  89.479317  [0, 22732, 0, 22733]   
2022-06-06 04:15:00  0.0  83.134895  0.0  90.309265  [0, 22732, 0, 22733]   
2022-06-06 04:30:00  0.0  83.929001  0.0  91.103371  [0, 22732, 0, 22733]   

                          actions                   mask_truth      load  \
time                                                                       
2022-01-01 00:00:00  [2, 1, 1, 0]  [False, False, False, True] -3.000962   
2022-01-01 00:15:00  [2, 1, 1, 0]  [False, False, False, True] -3.382362   
2022-01-01 00:30:00  [2, 1, 1, 0]  [False, False, False, True] -3.764104   
2022-01-01 00:45:00  [2, 1, 1, 0]  [False, False, False, True] -3.706225   
2022-01-01 01:00:00  [2, 0, 1, 0]   [False, True, False, True] -5.750331   
...                           ...                          ...       ...   
2022-06-06 03:30:00  [2, 1, 2, 1]   [False, True, False, True]  0.000000   
2022-06-06 03:45:00  [2, 1, 2, 1]   [False, True, False, True]  0.000000   
2022-06-06 04:00:00  [2, 1, 2, 1]   [False, True, False, True]  0.000000   
2022-06-06 04:15:00  [2, 1, 2, 1]   [False, True, False, True]  0.000000   
2022-06-06 04:30:00  [2, 1, 2, 1]  [False, True, False, False]  0.000000   

                     load_reward  EV_reward    rewards  
time                                                    
2022-01-01 00:00:00    -3.970603        0.0  -3.970603  
2022-01-01 00:15:00    -4.606839        0.0  -4.606839  
2022-01-01 00:30:00    -4.510376        0.0  -4.510376  
2022-01-01 00:45:00    -6.591210        0.0  -6.591210  
2022-01-01 01:00:00    -6.414302        0.0  -6.414302  
...                          ...        ...        ...  
2022-06-06 03:30:00    15.000000        0.0  15.000000  
2022-06-06 03:45:00    15.000000        0.0  15.000000  
2022-06-06 04:00:00    15.000000        0.0  15.000000  
2022-06-06 04:15:00    15.000000        0.0  15.000000  
2022-06-06 04:30:00    15.000000        0.0  15.000000  

[14995 rows x 11 columns]

In [119]:
env.plot_VPP_results()

In [120]:
env.plot_VPP_supply_demand()

In [121]:
env.plot_VPP_Elvis_comparison()

In [122]:
env.plot_rewards_results()

In [123]:
env.plot_rewards_stats()

In [124]:
env.plot_EVs_kpi()

In [125]:
env.plot_actions_kpi()

In [126]:
env.plot_load_kpi()

In [127]:
env.plot_yearly_load_log()

In [128]:
#env.close()